In [24]:
from rdkit import Chem
from rdkit.Chem.Scaffolds import MurckoScaffold
from collections import defaultdict
import random
import pandas as pd

In [25]:
def get_scaffold(smiles: str) -> str:
    mol = Chem.MolFromSmiles(smiles)
    scaffold = MurckoScaffold.GetScaffoldForMol(mol)
    return Chem.MolToSmiles(scaffold, canonical=True)


In [26]:
def scaffold_split(
    df,
    smiles_col="smiles",
    frac_train=0.8,
    seed=42
):
    random.seed(seed)

    scaffold_groups = defaultdict(list)
    for idx, row in df.iterrows():
        scaffold = get_scaffold(row[smiles_col])
        scaffold_groups[scaffold].append(idx)

    scaffolds = list(scaffold_groups.keys())
    random.shuffle(scaffolds)

    train_idx, test_idx = [], []
    n_total = len(df)
    n_train = int(frac_train * n_total)

    for scaffold in scaffolds:
        if len(train_idx) < n_train:
            train_idx.extend(scaffold_groups[scaffold])
        else:
            test_idx.extend(scaffold_groups[scaffold])

    return df.loc[train_idx], df.loc[test_idx]


In [27]:
clean_df = pd.read_csv("training_data.csv")
print(clean_df.columns)

train_df, val_df = scaffold_split(clean_df)


Index(['ACTIVITY', 'smiles'], dtype='object')


In [ ]:
from rdkit import Chem
from rdkit.Chem import AllChem, MACCSkeys, rdMolDescriptors
from rdkit.Avalon import pyAvalonTools
import numpy as np
import pandas as pd

def smiles_to_mol(smiles):
    return Chem.MolFromSmiles(smiles)

def fp_to_array(fp):
    return np.array(fp)

def generate_fingerprint(smiles_list, fp_type, nBits=1024):
    mols = [smiles_to_mol(s) for s in smiles_list]

    if fp_type == "ECFP4":
        fps = [AllChem.GetMorganFingerprintAsBitVect(m, 2, nBits=nBits) for m in mols]
    elif fp_type == "ECFP6":
        fps = [AllChem.GetMorganFingerprintAsBitVect(m, 3, nBits=nBits) for m in mols]
    elif fp_type == "MACCS":
        fps = [MACCSkeys.GenMACCSKeys(m) for m in mols]
    elif fp_type == "AtomPair":
        fps = [rdMolDescriptors.GetHashedAtomPairFingerprintAsBitVect(m, nBits=nBits) for m in mols]
    elif fp_type == "TopologicalTorsion":
        fps = [rdMolDescriptors.GetHashedTopologicalTorsionFingerprintAsBitVect(m, nBits=nBits) for m in mols]
    elif fp_type == "RDKit":
        fps = [Chem.RDKFingerprint(m) for m in mols]
    elif fp_type == "Avalon":
        fps = [pyAvalonTools.GetAvalonFP(m, nBits) for m in mols]
    elif fp_type == "descriptors_only":
        return None
    else:
        raise ValueError(fp_type)

    return np.array([fp_to_array(fp) for fp in fps])


In [29]:
print(1)

1


In [40]:
from mordred import Calculator, descriptors
from sklearn.feature_selection import VarianceThreshold, mutual_info_classif

import numpy as np
import pandas as pd
from mordred import Calculator, descriptors

def compute_mordred(smiles):
    mols = [smiles_to_mol(s) for s in smiles]
    valid_idx = [i for i, m in enumerate(mols) if m is not None]
    mols = [m for m in mols if m is not None]

    calc = Calculator(descriptors, ignore_3D=True)
    df = calc.pandas(mols)

    # SAFETY: if Mordred returned a tuple
    if isinstance(df, tuple):
        df = df[0]

    # only numerical columns
    df = df.select_dtypes(include=[np.number])

    # NaN / inf
    df = df.replace([np.inf, -np.inf], np.nan).fillna(0)

    return df.reset_index(drop=True), valid_idx


import numpy as np
import pandas as pd
from sklearn.feature_selection import VarianceThreshold, mutual_info_classif

def select_descriptors_mi_corr(
    X: pd.DataFrame,
    y: np.ndarray,
    k: int = 200,
    corr_threshold: float = 0.8
):
    """
    1) Remove zero-variance features
    2) Select top-k by Mutual Information
    3) Remove highly correlated features
    """

    # ---------- 1. Variance ----------
    vt = VarianceThreshold(0.0)
    X_v = vt.fit_transform(X)
    cols_v = X.columns[vt.get_support()]

    X_v = pd.DataFrame(X_v, columns=cols_v)

    # ---------- 2. Mutual Information ----------
    mi = mutual_info_classif(X_v, y, random_state=42)
    mi_series = pd.Series(mi, index=X_v.columns)
    
    top_cols = mi_series.sort_values(ascending=False).head(k).index
    X_mi = X_v[top_cols]
    print(f"len(mi_series): {len(mi_series)}")

    # ---------- 3. Correlation filtering ----------
    corr = X_mi.corr().abs()
    upper = corr.where(np.triu(np.ones(corr.shape), k=1).astype(bool))

    drop_cols = [
        col for col in upper.columns
        if any(upper[col] > corr_threshold)
    ]

    X_final = X_mi.drop(columns=drop_cols)

    return X_final



In [41]:
from sklearn.feature_selection import VarianceThreshold, mutual_info_classif

class DescriptorSelector:
    def __init__(self, k=None, corr_threshold=0.95):
        self.k = k
        self.corr_threshold = corr_threshold

        self.vt = VarianceThreshold(0.0)
        self.selected_columns_ = None
        self.mi_ranking_ = None

    def fit(self, X: pd.DataFrame, y: np.ndarray):
        # 1. Variance
        X_v = self.vt.fit_transform(X)
        cols_v = X.columns[self.vt.get_support()]
        X_v = pd.DataFrame(X_v, columns=cols_v, index=X.index)

        # 2. MI
        mi = mutual_info_classif(X_v, y, random_state=42)
        mi = pd.Series(mi, index=X_v.columns).sort_values(ascending=False)
        self.mi_ranking_ = mi

        # take all features, correlation filter will remove redundant ones
        X_mi = X_v[mi.index]

        # 3. Correlation prune (keep first = higher MI)
        corr = X_mi.corr().abs()
        upper = corr.where(np.triu(np.ones(corr.shape), k=1).astype(bool))

        drop_cols = [
            c for c in upper.columns
            if any(upper[c] > self.corr_threshold)
        ]

        kept = [c for c in X_mi.columns if c not in drop_cols]

        # 4. Top-K AFTER corr
        if self.k is not None:
            kept = kept[: self.k]

        self.selected_columns_ = kept
        return self

    def transform(self, X: pd.DataFrame):
        X_v = self.vt.transform(X)
        cols_v = X.columns[self.vt.get_support()]
        X_v = pd.DataFrame(X_v, columns=cols_v, index=X.index)

        return X_v[self.selected_columns_]


In [ ]:
def build_feature_matrix(
    smiles,
    y,
    fp_name,
    n_bits,
    descriptor_df=None,
    desc_k=200
):
    # Fingerprints
    X_fp = generate_fingerprint(smiles, fp_name, n_bits)

    if descriptor_df is None:
        return X_fp

    # Descriptor selection
    X_desc = select_descriptors_mi_corr(
        descriptor_df,
        y,
        k=desc_k,
        corr_threshold=0.95
    )

    # Combine
    X = np.hstack([X_fp, X_desc.values])

    return X


In [31]:
from sklearn.linear_model import LogisticRegression
from sklearn.ensemble import RandomForestClassifier
from xgboost import XGBClassifier
from lightgbm import LGBMClassifier


def model_factory(name: str, trial):
    if name == "LogReg":
        return LogisticRegression(
            C=trial.suggest_float("C", 1e-4, 10.0, log=True),
            penalty="l2",
            solver="lbfgs",
            max_iter=3000,
            random_state=42,
        )

    if name == "RF":
        return RandomForestClassifier(
            n_estimators=trial.suggest_int("n_estimators", 50, 800),
            max_depth=trial.suggest_int("max_depth", 3, 20),
            min_samples_split=trial.suggest_int("min_samples_split", 2, 20),
            min_samples_leaf=trial.suggest_int("min_samples_leaf", 1, 15),
            max_features=trial.suggest_categorical("max_features", ["sqrt", "log2"]),
            bootstrap=True,
            random_state=42,
            n_jobs=-1,
        )

    if name == "XGB":
        return XGBClassifier(
            n_estimators=trial.suggest_int("n_estimators", 50, 1000),
            max_depth=trial.suggest_int("max_depth", 3, 10),
            learning_rate=trial.suggest_float("learning_rate", 1e-3, 0.2, log=True),
            subsample=trial.suggest_float("subsample", 0.6, 1.0),
            colsample_bytree=trial.suggest_float("colsample_bytree", 0.6, 1.0),
            min_child_weight=trial.suggest_int("min_child_weight", 1, 10),
            gamma=trial.suggest_float("gamma", 0.0, 5.0),
            reg_alpha=trial.suggest_float("reg_alpha", 1e-8, 10.0, log=True),
            reg_lambda=trial.suggest_float("reg_lambda", 1e-8, 10.0, log=True),
            eval_metric="logloss",
            tree_method="hist",
            random_state=42,
            n_jobs=-1,
        )

    if name == "LGBM":
        return LGBMClassifier(
            n_estimators=trial.suggest_int("n_estimators", 300, 1000),
            learning_rate=trial.suggest_float("learning_rate", 1e-3, 0.2, log=True),
            num_leaves=trial.suggest_int("num_leaves", 16, 128),
            max_depth=trial.suggest_int("max_depth", 3, 12),
            min_child_samples=trial.suggest_int("min_child_samples", 10, 100),
            subsample=trial.suggest_float("subsample", 0.6, 1.0),
            colsample_bytree=trial.suggest_float("colsample_bytree", 0.6, 1.0),
            reg_alpha=trial.suggest_float("reg_alpha", 1e-8, 10.0, log=True),
            reg_lambda=trial.suggest_float("reg_lambda", 1e-8, 10.0, log=True),
            random_state=42,
            n_jobs=-1,
        )

    raise ValueError(f"Unknown model name: {name}")


In [32]:
import optuna
from sklearn.model_selection import StratifiedKFold
from sklearn.metrics import (
    roc_auc_score,
    f1_score,
    precision_score,
    recall_score,
    accuracy_score,
)



def compute_metrics(y_true, y_proba, threshold=0.5):
    y_pred = (y_proba >= threshold).astype(int)

    return {
        "roc_auc": roc_auc_score(y_true, y_proba),
        "f1": f1_score(y_true, y_pred),
        "precision": precision_score(y_true, y_pred),
        "recall": recall_score(y_true, y_pred),
        "accuracy": accuracy_score(y_true, y_pred),
    }


def objective(trial, X_train, y_train, X_val, y_val, model_name):
    model = model_factory(model_name, trial)

    model.fit(X_train, y_train)

    y_val_proba = model.predict_proba(X_val)[:, 1]
    y_train_proba = model.predict_proba(X_train)[:, 1]

    val_metrics = compute_metrics(y_val, y_val_proba)
    train_metrics = compute_metrics(y_train, y_train_proba)

    # =====================
    # Store extra metrics
    # =====================
    for k, v in val_metrics.items():
        trial.set_user_attr(f"val_{k}", v)

    for k, v in train_metrics.items():
        trial.set_user_attr(f"train_{k}", v)

    trial.set_user_attr(
        "f1_gap",
        train_metrics["f1"] - val_metrics["f1"]
    )

    auc = roc_auc_score(y_val, y_val_proba)

    return auc


In [ ]:
import mlflow

def run_experiment(fp_name, model_name, X_train, y_train, X_val, y_val, n_trials=30, include_1d_descriptor=False, experiment_name="n_bits=1024_number_of_descriptors", n_descriptors=0):
    study = optuna.create_study(direction="maximize")
    study.optimize(lambda t: objective(t, X_train, y_train, X_val, y_val, model_name), n_trials=n_trials)

    with mlflow.start_run(run_name=f"{fp_name}_{model_name}_{experiment_name}"):
        mlflow.log_param("fingerprint", fp_name)
        mlflow.log_param("model", model_name)
        mlflow.log_params(study.best_params)
        mlflow.log_param("total_n_bits", X_train.shape[1])
        if include_1d_descriptor:
            mlflow.log_param("include_1d_descriptor", True)
            mlflow.log_param("n_descriptors", n_descriptors)
        else:
            mlflow.log_param("include_1d_descriptor", False)
        mlflow.log_metric("roc_auc_best", study.best_value)

        # --------
        # Metrics (validation)
        # --------
        for k, v in study.best_trial.user_attrs.items():
            if k.startswith("val_"):
                mlflow.log_metric(k, v)

        # --------
        # Metrics (train)
        # --------
        for k, v in study.best_trial.user_attrs.items():
            if k.startswith("train_"):
                mlflow.log_metric(k, v)

        # --------
        # Extra diagnostics
        # --------
        if "f1_gap" in study.best_trial.user_attrs:
            mlflow.log_metric(
                "f1_gap",
                study.best_trial.user_attrs["f1_gap"],
            )

    return study.best_value


In [ ]:
fingerprints = [
    "descriptors_only", "ECFP4", "ECFP6", "MACCS",
    "AtomPair", "TopologicalTorsion", "RDKit", "Avalon"
]

include_descriptors = False

models = ["LogReg", "RF", "XGB", "LGBM"]

results = []

mlflow.set_experiment("chem_suggested_fingerprints_1024bits_2")

for fp in fingerprints:
    # X_train = build_feature_matrix(smiles=train_df["smiles"], y=train_df["ACTIVITY"], fp_name=fp, n_bits=1024, descriptor_df=None, desc_k=200)
    if fp != "descriptors_only":
        X_train = generate_fingerprint(smiles=train_df["smiles"], fp_type=fp, nBits=1024)
    else:
        X_train = None
    y_train = train_df["ACTIVITY"].values

    # X_val = build_feature_matrix(smiles=val_df["smiles"], y=val_df["ACTIVITY"], fp_name=fp, n_bits=1024, descriptor_df=None, desc_k=200)
    if fp != "descriptors_only":
        X_val = generate_fingerprint(smiles=val_df["smiles"], fp_type=fp, nBits=1024)
    else:
        X_val = None
    y_val = val_df["ACTIVITY"].values

    for model in models:
        score = run_experiment(fp, model, X_train, y_train, X_val, y_val, include_1d_descriptor=False, experiment_name="n_bits=1024")
        results.append({
            "Fingerprint": fp,
            "Model": model,
            "ROC_AUC": score
        })

pd.DataFrame(results).sort_values("ROC_AUC", ascending=False)


2026/01/28 18:45:51 INFO mlflow.tracking.fluent: Experiment with name 'chem_suggested_fingerprints_1024bits_2' does not exist. Creating a new experiment.
[I 2026-01-28 18:46:00,100] A new study created in memory with name: no-name-ea69c490-fb0d-46a6-bb86-c6625eb020fc
[I 2026-01-28 18:46:00,279] Trial 0 finished with value: 0.7420555591095189 and parameters: {'C': 0.0012662112298162543}. Best is trial 0 with value: 0.7420555591095189.
[I 2026-01-28 18:46:00,817] Trial 1 finished with value: 0.7888404176746999 and parameters: {'C': 0.17804483880416644}. Best is trial 1 with value: 0.7888404176746999.
[I 2026-01-28 18:46:01,410] Trial 2 finished with value: 0.7867591682562576 and parameters: {'C': 0.268806035952511}. Best is trial 1 with value: 0.7888404176746999.
[I 2026-01-28 18:46:01,801] Trial 3 finished with value: 0.7948297344607798 and parameters: {'C': 0.0520791748577683}. Best is trial 3 with value: 0.7948297344607798.
[I 2026-01-28 18:46:02,085] Trial 4 finished with value: 0.79

[LightGBM] [Info] Number of positive: 4906, number of negative: 4639
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.012453 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 2036
[LightGBM] [Info] Number of data points in the train set: 9545, number of used features: 1018
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.513986 -> initscore=0.055960
[LightGBM] [Info] Start training from score 0.055960
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: 

d:\programs\miniconda\envs\chem_ml\lib\site-packages\sklearn\utils\deprecation.py:132: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
d:\programs\miniconda\envs\chem_ml\lib\site-packages\sklearn\utils\deprecation.py:132: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
[I 2026-01-28 18:49:09,618] Trial 0 finished with value: 0.791961201381781 and parameters: {'n_estimators': 931, 'learning_rate': 0.002439501305225727, 'num_leaves': 86, 'max_depth': 6, 'min_child_samples': 43, 'subsample': 0.6438954814723351, 'colsample_bytree': 0.6927895276638518, 'reg_alpha': 0.010168060495987877, 'reg_lambda': 0.0003168598211517006}. Best is trial 0 with value: 0.791961201381781.
d:\programs\miniconda\envs\chem_ml\lib\site-packages\sklearn\utils\deprecation.py:132: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be remov

[LightGBM] [Info] Number of positive: 4906, number of negative: 4639
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.011626 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 2034
[LightGBM] [Info] Number of data points in the train set: 9545, number of used features: 1017
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.513986 -> initscore=0.055960
[LightGBM] [Info] Start training from score 0.055960
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: 

d:\programs\miniconda\envs\chem_ml\lib\site-packages\sklearn\utils\deprecation.py:132: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
d:\programs\miniconda\envs\chem_ml\lib\site-packages\sklearn\utils\deprecation.py:132: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
[I 2026-01-28 18:49:10,439] Trial 1 finished with value: 0.840396956708849 and parameters: {'n_estimators': 901, 'learning_rate': 0.0579911214213479, 'num_leaves': 123, 'max_depth': 5, 'min_child_samples': 47, 'subsample': 0.7238168148485303, 'colsample_bytree': 0.8562923568824234, 'reg_alpha': 0.682855450480513, 'reg_lambda': 0.7474468596390178}. Best is trial 1 with value: 0.840396956708849.
d:\programs\miniconda\envs\chem_ml\lib\site-packages\sklearn\utils\deprecation.py:132: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1

...

[LightGBM] [Info] Number of positive: 4906, number of negative: 4639
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.019472 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 2028
[LightGBM] [Info] Number of data points in the train set: 9545, number of used features: 1014
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.513986 -> initscore=0.055960
[LightGBM] [Info] Start training from score 0.055960
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: 

d:\programs\miniconda\envs\chem_ml\lib\site-packages\sklearn\utils\deprecation.py:132: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
d:\programs\miniconda\envs\chem_ml\lib\site-packages\sklearn\utils\deprecation.py:132: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
[I 2026-01-28 19:22:28,906] Trial 28 finished with value: 0.8711602656555317 and parameters: {'n_estimators': 672, 'learning_rate': 0.05253668035728278, 'num_leaves': 33, 'max_depth': 5, 'min_child_samples': 71, 'subsample': 0.7676195953913536, 'colsample_bytree': 0.7738452129388613, 'reg_alpha': 0.02211691357402265, 'reg_lambda': 1.1304683456909655e-06}. Best is trial 9 with value: 0.8810950875825811.
d:\programs\miniconda\envs\chem_ml\lib\site-packages\sklearn\utils\deprecation.py:132: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be rem

[LightGBM] [Info] Number of positive: 4906, number of negative: 4639
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.020260 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 2044
[LightGBM] [Info] Number of data points in the train set: 9545, number of used features: 1022
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.513986 -> initscore=0.055960
[LightGBM] [Info] Start training from score 0.055960


d:\programs\miniconda\envs\chem_ml\lib\site-packages\sklearn\utils\deprecation.py:132: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
d:\programs\miniconda\envs\chem_ml\lib\site-packages\sklearn\utils\deprecation.py:132: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
[I 2026-01-28 19:22:31,818] Trial 29 finished with value: 0.8545153589373777 and parameters: {'n_estimators': 646, 'learning_rate': 0.007276802722267741, 'num_leaves': 43, 'max_depth': 11, 'min_child_samples': 31, 'subsample': 0.9216273651823523, 'colsample_bytree': 0.9129110180399032, 'reg_alpha': 0.2166362818482198, 'reg_lambda': 0.0042337727823382}. Best is trial 9 with value: 0.8810950875825811.


Fingerprint   Model   ROC_AUC
26              Avalon     XGB  0.884694
27              Avalon    LGBM  0.881095
22               RDKit     XGB  0.876056
14            AtomPair     XGB  0.875812
25              Avalon      RF  0.875305
23               RDKit    LGBM  0.873767
15            AtomPair    LGBM  0.872718
10               MACCS     XGB  0.871172
19  TopologicalTorsion    LGBM  0.870468
11               MACCS    LGBM  0.870245
9                MACCS      RF  0.864465
18  TopologicalTorsion     XGB  0.863606
3                ECFP4    LGBM  0.863102
2                ECFP4     XGB  0.862846
13            AtomPair      RF  0.862844
6                ECFP6     XGB  0.862438
7                ECFP6    LGBM  0.860432
21               RDKit      RF  0.860328
17  TopologicalTorsion      RF  0.847603
5                ECFP6      RF  0.846330
1                ECFP4      RF  0.834838
20               RDKit  LogReg  0.810830
24              Avalon  LogReg  0.805248
16  TopologicalTorsion  LogReg  0.801756
4                ECFP6  LogReg  0.797213
0                ECFP4  LogReg  0.795316
12            AtomPair  LogReg  0.776562
8                MACCS  LogReg  0.753734

In [ ]:
fingerprints = [
    "descriptors_only", "MACCS",
    "AtomPair", "TopologicalTorsion", "RDKit", "Avalon"
]

num_descriptors = [5, 10, 20, 50, 100, 150, 200, 300, 400, 500]

include_descriptors = False

models = ["RF", "XGB", "LGBM"]

results = []

mlflow.set_experiment("chem_suggested_fingerprints_1024bits_2")

for fp in fingerprints:
    # X_train = build_feature_matrix(smiles=train_df["smiles"], y=train_df["ACTIVITY"], fp_name=fp, n_bits=1024, descriptor_df=None, desc_k=200)
    if fp != "descriptors_only":
        X_train = generate_fingerprint(smiles=train_df["smiles"], fp_type=fp, nBits=1024)
    else:
        X_train = None
    y_train = train_df["ACTIVITY"].values

    # X_val = build_feature_matrix(smiles=val_df["smiles"], y=val_df["ACTIVITY"], fp_name=fp, n_bits=1024, descriptor_df=None, desc_k=200)
    if fp != "descriptors_only":
        X_val = generate_fingerprint(smiles=val_df["smiles"], fp_type=fp, nBits=1024)
    else:
        X_val = None
    y_val = val_df["ACTIVITY"].values

    for model in models:
        score = run_experiment(fp, model, X_train, y_train, X_val, y_val, include_1d_descriptor=False, experiment_name="n_bits=1024")
        results.append({
            "Fingerprint": fp,
            "Model": model,
            "ROC_AUC": score
        })

pd.DataFrame(results).sort_values("ROC_AUC", ascending=False)


In [42]:
# Mordred
X_train_mordred, idx_train = compute_mordred(train_df["smiles"])
y_train = train_df.loc[idx_train, "ACTIVITY"].values


 32%|███▏      | 3087/9545 [04:28<15:32,  6.93it/s]

d:\programs\miniconda\envs\chem_ml\lib\site-packages\numpy\core\fromnumeric.py:88: RuntimeWarning: overflow encountered in reduce
  return ufunc.reduce(obj, axis, dtype, out, **passkwargs)


 40%|███▉      | 3771/9545 [05:28<16:40,  5.77it/s]

d:\programs\miniconda\envs\chem_ml\lib\site-packages\numpy\core\fromnumeric.py:88: RuntimeWarning: overflow encountered in reduce
  return ufunc.reduce(obj, axis, dtype, out, **passkwargs)


 49%|████▊     | 4647/9545 [06:48<04:48, 16.95it/s]

...

d:\programs\miniconda\envs\chem_ml\lib\site-packages\numpy\core\fromnumeric.py:88: RuntimeWarning: overflow encountered in reduce
  return ufunc.reduce(obj, axis, dtype, out, **passkwargs)


 93%|█████████▎| 8904/9545 [13:10<01:01, 10.35it/s]

d:\programs\miniconda\envs\chem_ml\lib\site-packages\numpy\core\fromnumeric.py:88: RuntimeWarning: overflow encountered in reduce
  return ufunc.reduce(obj, axis, dtype, out, **passkwargs)


100%|██████████| 9545/9545 [14:07<00:00, 11.27it/s]


KeyError: '[3, 4, 9, 13, 17, 21, 26, 29, 45, 48, 53, 58, 64, 66, 76, 79, 83, 94, 99, 101, 104, 113, 116, 121, 126, 143, 160, 161, 162, 169, 172, 175, 176, 183, 194, 199, 208, 212, 214, 221, 222, 230, 233, 235, 239, 241, 252, 253, 254, 262, 273, 277, 280, 282, 284, 288, 294, 320, 321, 326, 330, 340, 344, 350, 354, 355, 357, 359, 367, 373, 392, 394, 398, 400, 409, 412, 413, 415, 422, 423, 444, 455, 456, 460, 462, 466, 470, 474, 490, 494, 495, 497, 499, 512, 513, 516, 520, 522, 524, 530, 535, 536, 537, 539, 545, 550, 553, 556, 564, 568, 579, 584, 586, 598, 601, 605, 608, 620, 627, 631, 632, 633, 634, 635, 638, 641, 642, 644, 646, 655, 656, 657, 659, 660, 663, 671, 674, 680, 685, 686, 695, 697, 699, 701, 706, 721, 734, 736, 744, 747, 748, 751, 753, 756, 760, 765, 766, 773, 781, 785, 789, 792, 795, 799, 805, 815, 819, 829, 836, 844, 853, 855, 860, 868, 869, 878, 882, 885, 886, 887, 888, 890, 897, 922, 924, 925, 933, 938, 940, 941, 947, 951, 956, 961, 964, 965, 966, 971, 975, 980, 983, 986, 

In [43]:
print(X_train_mordred)
print(len(X_train_mordred.columns))

      nAcid  nBase    SpAbs_A   SpMax_A  SpDiam_A     SpAD_A   SpMAD_A  \
0         0      1  37.123980  2.496621  4.896005  37.123980  1.325856   
1         0      1  37.034588  2.483468  4.875633  37.034588  1.277055   
2         0      1  38.559577  2.496453  4.896365  38.559577  1.285319   
3         0      3  32.545868  2.407870  4.812980  32.545868  1.301835   
4         0      3  31.432141  2.407854  4.812946  31.432141  1.309673   
...     ...    ...        ...       ...       ...        ...       ...   
9540      0      3  33.540889  2.337583  4.675166  33.540889  1.290034   
9541      0      0  57.915833  2.383932  4.767864  57.915833  1.259040   
9542      0      3  51.071199  2.539028  5.078056  51.071199  1.245639   
9543      0      1  38.059829  2.460270  4.810866  38.059829  1.359280   
9544      0      1  39.764907  2.460967  4.816596  39.764907  1.371204   

       LogEE_A     VE1_A     VE2_A  ...      SRW10     TSRW10          MW  \
0     4.269490  4.148598  0.148164

In [ ]:
# Selector
selector = DescriptorSelector(
    k=300,
    corr_threshold=0.95
)

X_train_sel = selector.fit_transform(X_train_mordred, y_train)
print(len(X_train_sel.columns))